# Scikit-learn 4

Cross Validation, Hyperparameter Search

## 1 Cross-validation

Until now, we have assigned observations to the training or test set at random. This creates some unwanted variance, as our model could be trained on easy examples and tested on hard ones, or vice versa - purely by chance. Cross-validation is a method to overcome this difficulty. The idea is to divide all the data into _k_ parts (for example, 3) and then train several models, each time holding out 1 part to test on, and train on the remaining 2.

![Screen%20Shot%202019-01-28%20at%2011.54.45.png](attachment:Screen%20Shot%202019-01-28%20at%2011.54.45.png)

Load the iris data set and store the data in `X` and `y`:

Look at the first examples and check the shapes to make sure everything is loaded correctly:

### Notion of data folds

For cross-validation, the entire data set is split into equal parts that are called "folds". In `scikit-learn`, the procedure builds on a class called `KFold`:

In [0]:
from sklearn.model_selection import KFold
kf = KFold(n_splits=5, shuffle=True)

In this case, we will split the data into 5 folds of the same size. Instead of splitting the data right away, the object just returns _indexes_ that can be used to extract parts of `X` and `y:`

In [0]:
indexes = kf.split(X, y)
print(indexes)
for train_indexes, test_indexes in indexes:
    print((train_indexes, test_indexes))

More concretely, the `split` method of a `KFold` object returns lists of indexes that can be used to index the `X` and `y` arrays like so:

In [0]:
# exploiting the fact that loop variables leak into the outer environment
print(train_indexes)
print()
print(X[train_indexes])

### Automatic folds and cross-validation

The process of assigning observations to folds, training models and testing them on the respective portion that was held out (the examples at the test set indexes) can be automated of course.

To perform cross-validation, we need to train a model of course. The classification algorithm we use here is a "multi-layer perceptron" or "MLP". Import the class `MLPClassifier` from `scikit-learn`:

Make an instance of this class, assign to the variable `mlp` and print it. Printing it will show you several hyperparameters that were initialized to their default values (we did not set any explicitly):

Now we can use this estimator for cross-validation:

In [0]:
# 10-fold cross-validation with `cross_val_score`
from sklearn.model_selection import cross_val_score
scores = cross_val_score(mlp, X, y, cv=10, scoring='accuracy')
print(scores)

This gives an accuracy score for each time data was split into training and testing examples. Averaging them will give a better (= more smooth) estimate of generalization, or "out-of-sample performance". Compute the mean of `scores`:

**Question for you: what is a reasonable number of folds k, for k-fold cross validation?**

## 2 Search for Hyperparameters

Until now, when we initialized estimators (like KNN, or MLP) we simply brushed over the fact that certain parameters need to be set. For instance, KNN needs the number of neighbors `n_neighbors`, and an MLP very typically needs to know the dimensions of hidden layers, `hidden_layer_sizes`.

Using the toolset we have aquired until now, we can loop over different values of those so-called **hyperparameters** and get a mean cross-validation score in each iteration:

In [0]:
# search for an optimal value of hidden layer size for MLP:
layer_size_range = range(50, 160, 10)
print(layer_size_range)

mean_scores = []

for s in layer_size_range:
    mlp = MLPClassifier(hidden_layer_sizes=(s))
    scores = cross_val_score(mlp, X, y, cv=10, scoring='accuracy')
    mean_scores.append(scores.mean())

print(mean_scores)

As you can see, setting the hyperparameter `hidden_layer_sizes` to a reasonable value is crucial to get a good accuracy score:

In [0]:
%matplotlib inline
import matplotlib.pyplot as plt
import numpy as np

fig = plt.figure(figsize=(6,6))

plt.plot(layer_size_range, mean_scores)

def annot_max(x,y, ax=None):
    """
    This code is adapted from:
    https://stackoverflow.com/a/43375318/1987598
    """
    xmax = x[np.argmax(y)]
    ymax = max(y)
    text= "s={}, accuracy={:.3f}".format(xmax, ymax)
    if not ax:
        ax = plt.gca()
    bbox_props = dict(boxstyle="square,pad=0.3", fc="w", ec="k", lw=0.72)
    arrowprops = dict(arrowstyle="->",connectionstyle="angle,angleA=0,angleB=-60")
    kw = dict(xycoords='data',textcoords="axes fraction",
              arrowprops=arrowprops, bbox=bbox_props, ha="right", va="top")
    ax.annotate(text, xy=(xmax, ymax), xytext=(0.85,0.50), **kw)

annot_max(layer_size_range, mean_scores)

plt.xlabel('Value of s for hidden layer size')
plt.ylabel('Cross-validated accuracy')

Which means that if we choose arbitrary values for hyperparameters, it is likely that performance will suffer. Still, we would not want to search for optimal values manually, `scikit-learn` offers methods to automatically search for them.

**Question for you: in your opinion, is the choice of classifier itself a hyperparameter that should be optimized?**

## 3 Automated Hyperparameter Search


### Grid search for hyperparameter values

A straightforward way to search for an optimal hyperparameter value ("hyperparameter tuning") is to define the set of values that should be tried and from this set choose the one that gives the highest cross-validation score. If several hyperparameters need to be optimized, all permutations need to be tried. This method is called **grid search**.

We now employ grid search with cross-validation to automate the procedure above that finds an optimal value for MLP hidden layer size:

In [0]:
from sklearn.model_selection import GridSearchCV

layer_size_range = range(20, 110, 10)

# define parameters whose value space needs to be searched
param_grid = {'hidden_layer_sizes': layer_size_range}
print(param_grid)

# create estimator object, default values
mlp = MLPClassifier()

# instantiate grid search class
grid = GridSearchCV(mlp, param_grid, cv=10, scoring='accuracy', n_jobs=2, return_train_score=True)

# fit iris data (reload if you modified those variables)
grid.fit(X, y)

Results are stored in `grid.cv_results_`:

In [0]:
# a bit unwieldy
# print(grid.cv_results_)

The data can be converted to a pandas data frame for easier inspection. Import pandas with the abbreviation `pd:`

In [0]:
df = pd.DataFrame.from_dict(grid.cv_results_)
df.sort_values(by=["rank_test_score"])

In the course of grid search, the grid is automatically refit with the best parameter values and all of the training examples (so that you would not waste data). Predictions can be made directly with the `grid` object, in the usual fashion:

In [0]:
grid.predict([[0.2, 0.5, 0.6, 0.8]])

**Question for you: What is a potential problem with grid search?**

###  Random search as an efficient approximation to grid search

For large models, a high number of parameters or high range of values, grid search can be computationally expensive. Searching for values would be more efficient if it were not _exhaustive_, that is, if only a subset of value combinations would be cross-validated. Such a method is called **random(ized) search**.

In [0]:
import scipy
from sklearn.model_selection import RandomizedSearchCV

# bigger search space
layer_size_range = range(20, 110, 10)
solver_values = ['lbfgs', 'sgd', 'adam']
learning_rate_init_dist = scipy.stats.truncnorm(a=0, b=np.inf, loc=0.01, scale=0.1)

# define parameters whose value space needs to be searched
param_grid = {'hidden_layer_sizes': layer_size_range,
              'solver': solver_values,
              'learning_rate_init': learning_rate_init_dist}

random_search = RandomizedSearchCV( estimator=mlp,
                                    param_distributions=param_grid,
                                    n_iter=10,
                                    cv=10,
                                    scoring='accuracy',
                                    n_jobs=2,
                                    return_train_score=True,
                                    random_state=42)

# fit iris data (reload if you modified those variables)
random_search.fit(X, y)

In [0]:
# inspect the results
pd.options.display.max_colwidth = 100 

df = pd.DataFrame.from_dict(random_search.cv_results_)
df.sort_values(by=["rank_test_score"])

Here is a worthwhile article about the differences between grid search and random search: https://medium.com/rants-on-machine-learning/smarter-parameter-sweeps-or-why-grid-search-is-plain-stupid-c17d97a0e881.

### Quick access to best estimator and parameters

Instead of a tabular overview, you can of course quickly access the best estimator and the mean score (mean over all cross-validated folds) obtained by this estimator. Here are some useful outcomes:

In [0]:
print(random_search.best_estimator_) # convention: variables computed by `scikit-learn` end in "_"
print(random_search.best_score_)
print(random_search.best_params_)

## 4 Splitting data into training, development and testing

Until now, we have split data into training and testing. We used test data for parameter optimization. By the time we arrive at optimal parameter values, we will have had many passes through test data. Because of that, some people would argue, the final accuracy score is not really _out-of-sample_.

An even better estimate of true generalization error is obtained when the test set is truly held out, i.e. never shown to the model until the final testing round. In `scikit-learn`, this means splitting the data into training and testing parts, and then do search and cross-validation on the training part only. During cross-validation, a fraction of the training set will implicitly become the _development_ or _validation_ set.

![Screen%20Shot%202019-01-28%20at%2011.53.50.png](attachment:Screen%20Shot%202019-01-28%20at%2011.53.50.png)

**Task for you: implement the idea described in the paragraph above, using the `iris` data set.**